In [1]:
# Dependencies
import pandas as pd
import scipy.stats as st
import numpy as np
from config import javi_api
import requests
import json
from census import Census
import matplotlib.pyplot as plt
from config import majo_api


In [2]:
# Read in the presidential elections data set
taxbystate = pd.read_csv('../Input/tax_state.csv')
taxbystate

State Gasoline Tax / gallon
0                Alabama                $0.28 
1                 Alaska                $0.09 
2                Arizona                $0.18 
3               Arkansas                $0.25 
4             California                $0.54 
5               Colorado                $0.22 
6            Connecticut                $0.10 
7               Delaware                $0.23 
8   District of Columbia                $0.34 
9                Florida                $0.35 
10               Georgia                $0.31 
11                Hawaii                $0.16 
12                 Idaho                $0.32 
13              Illinois                $0.42 
14               Indiana                $0.33 
15                  Iowa                $0.27 
16                Kansas                $0.24 
17              Kentucky                $0.25 
18             Louisiana                $0.20 
19                 Maine                $0.30 
20              Maryland                $0.43 
21         Massachusetts                $0.24 
22              Michigan                $0.29 
23             Minnesota                $0.29 
24           Mississippi                $0.18 
25              Missouri                $0.22 
26               Montana                $0.33 
27              Nebraska                $0.29 
28                Nevada                $0.23 
29         New Hampshire                $0.22 
30            New Jersey                $0.42 
31            New Mexico                $0.17 
32              New York                $0.18 
33        North Carolina                $0.41 
34          North Dakota                $0.23 
35                  Ohio                $0.39 
36              Oklahoma                $0.19 
37                Oregon                $0.38 
38          Pennsylvania                $0.61 
39          Rhode Island                $0.34 
40        South Carolina                $0.28 
41          South Dakota                $0.28 
42             Tennessee                $0.26 
43                 Texas                $0.20 
44                  Utah                $0.36 
45               Vermont                $0.36 
46              Virginia                $0.28 
47            Washington                $0.49 
48         West Virginia                $0.37 
49             Wisconsin                $0.31 
50               Wyoming                $0.24

In [3]:
params={
    "fuel_type":"ELEC",
    "limit":"all",
    "country":"US",
    "access":"public",
    "api_key":javi_api

}
url=f"https://developer.nrel.gov/api/alt-fuel-stations/v1.json?"
data=requests.get(url,params=params).json()
data

{'station_locator_url': 'https://afdc.energy.gov/stations/',
 'total_results': 54987,
 'station_counts': {'total': 138281,
  'fuels': {'BD': {'total': 0},
   'E85': {'total': 0},
   'ELEC': {'total': 138281, 'stations': {'total': 54987}},
   'HY': {'total': 0},
   'LNG': {'total': 0},
   'CNG': {'total': 0},
   'LPG': {'total': 0},
   'RD': {'total': 0}}},
 'fuel_stations': [{'access_code': 'public',
   'access_days_time': '5:30am-9pm; pay lot',
   'access_detail_code': None,
   'cards_accepted': None,
   'date_last_confirmed': '2023-01-10',
   'expected_date': None,
   'fuel_type_code': 'ELEC',
   'groups_with_access_code': 'Public',
   'id': 1523,
   'open_date': '1995-08-30',
   'owner_type_code': 'P',
   'status_code': 'E',
   'restricted_access': False,
   'station_name': 'Los Angeles Convention Center',
   'station_phone': '213-741-1151',
   'updated_at': '2023-02-14T15:54:11Z',
   'facility_type': 'PARKING_GARAGE',
   'geocode_status': 'GPS',
   'latitude': 34.040539,
   'longit

In [4]:
all_stations_df=pd.DataFrame(data["fuel_stations"])
all_stations_df.head()

access_code           access_days_time access_detail_code cards_accepted  \
0      public        5:30am-9pm; pay lot               None           None   
1      public             24 hours daily               None           None   
2      public             24 hours daily               None           None   
3      public  Dealership business hours               CALL           None   
4      public             6am-12am daily               None           None   

  date_last_confirmed expected_date fuel_type_code groups_with_access_code  \
0          2023-01-10          None           ELEC                  Public   
1          2022-09-14          None           ELEC                  Public   
2          2023-01-10          None           ELEC                  Public   
3          2021-12-09          None           ELEC     Public - Call ahead   
4          2020-02-06          None           ELEC                  Public   

     id   open_date  ... rd_blends_fr rd_blended_with_biodiesel  \
0  1523  1995-08-30  ...         None                      None   
1  1583  1996-10-15  ...         None                      None   
2  6355  1997-07-30  ...         None                      None   
3  6405  2012-12-11  ...         None                      None   
4  6425  1997-08-30  ...         None                      None   

  rd_max_biodiesel_level access_days_time_fr intersection_directions_fr  \
0                   None                None                       None   
1                   None                None                       None   
2                   None                None                       None   
3                   None                None                       None   
4                   None                None                       None   

  bd_blends_fr   groups_with_access_code_fr ev_pricing_fr  ev_network_ids  \
0         None                       Public          None             NaN   
1         None                       Public          None             NaN   
2         None                       Public          None             NaN   
3         None  Public - Appeler à l'avance          None             NaN   
4         None                       Public          None             NaN   

   federal_agency  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  

[5 rows x 68 columns]

In [5]:
reduced_df=all_stations_df[['station_name','facility_type','latitude', 'longitude','state','ev_dc_fast_num', 'ev_level1_evse_num',
       'ev_level2_evse_num', 'ev_other_evse', 'ev_network','ev_pricing']]
reduced_df["ev_pricing"].unique()

array(['Free; parking fee', 'Free',
       '$1 for the first two hours, $2 each additional hour; parking fee',
       None, '$2 service fee + $0.45 per kWh', '$12 parking fee',
       '$7 per session', 'Free; parking is $8 per day.',
       '$0.30 per kWh; $0.45 per kWh from 4pm-9pm',
       '$1 per hour for first two hours; $3 per hour thereafter',
       'Free; $6.00 for parking day pass for non-permit holders',
       '$20 parking fee', 'Parking fee',
       "Pay for garage' charging is free",
       'Free; 3 hour maximum charging session', '$1.50/hr',
       '$2 parking fee', '$0.75 per hour parking fee',
       '$1 per first and second half-hour parking fee; $1 per each additional hour parking fee',
       '$0.18 per kWh for first four hours; additional $25 fee after four hours',
       'Free; metered parking', 'Free; meter charge', '$10 per session',
       'Free for guests; $10 for non-guests', '$5 per hour',
       '$5 per session, customers pay up to $20 for leaving car connec

In [6]:
reduced_df["ev_pricing"][reduced_df["ev_pricing"]=="Free"].count()

9041

In [7]:
reduced_df.to_csv("../Resources/stations.csv")

In [8]:
#Create a variable specifying electric and hybrid vehicles only
technology="hy,elec,phev,hev,nevs"
url=f"https://developer.nrel.gov/api/transportation-incentives-laws/v1.json?api_key={javi_api}&technology={technology}"
data=requests.get(url).json()
data

{'metadata': {'version': '1.0.0', 'count': 1313},
 'inputs': {'technology': 'hy,elec,phev,hev,nevs'},
 'result': [{'id': 284,
   'state': 'US',
   'title': 'Congestion Mitigation and Air Quality (CMAQ) Improvement Program',
   'text': '<p>The CMAQ Program provides funding to state departments of transportation (DOTs), local governments, and transit agencies for projects and programs that help meet the requirements of the Clean Air Act by reducing mobile source emissions and regional congestion on transportation networks. Eligible activities include transit improvements, travel demand management strategies, congestion relief efforts (such as high occupancy vehicle lanes), diesel retrofit projects, alternative fuel vehicles and infrastructure, and medium- or heavy-duty zero emission vehicles and related charging equipment. Projects supported with CMAQ funds must demonstrate emissions reductions, be located in or benefit a U.S. Environmental Protection Agency-designated nonattainment or m

In [9]:
#Out of the collected data
incentives_df=pd.DataFrame(data["result"])
incentives_df.head()

id state                                              title  \
0  284    US  Congestion Mitigation and Air Quality (CMAQ) I...   
1  288    US                     Clean Cities Coalition Network   
2  317    US                 State Energy Program (SEP) Funding   
3  319    US                 Alternative Fuel Excise Tax Credit   
4  323    US                                   Clean School Bus   

                                                text          enacted_date  \
0  <p>The CMAQ Program provides funding to state ...  2005-08-10T00:00:00Z   
1  The mission of Clean Cities Coalition Network ...                  None   
2  The SEP provides grants to states to assist in...                  None   
3  <p>NOTE: This incentive was originally set to ...  2005-08-10T00:00:00Z   
4  <p>The U.S. Environmental Protection Agency’s ...                  None   

           amended_date                                          plaintext  \
0  2021-11-15T00:00:00Z  The CMAQ Program provides funding to state dep...   
1                  None  The mission of Clean Cities Coalition Network ...   
2  2021-11-15T00:00:00Z  The SEP provides grants to states to assist in...   
3  2022-08-16T00:00:00Z  NOTE: This incentive was originally set to exp...   
4  2021-11-15T00:00:00Z  The U.S. Environmental Protection Agency's (EP...   

   is_recent  seq_num        type                                agency  \
0      False     54.0  Incentives     U.S. Department of Transportation   
1      False     21.0    Programs             U.S. Department of Energy   
2      False     26.0  Incentives             U.S. Department of Energy   
3      False     11.0  Incentives         U.S. Internal Revenue Service   
4      False     33.0  Incentives  U.S. Environmental Protection Agency   

  significant_update_date recent_update_or_new  utility_id  \
0              11/29/2021               update         NaN   
1                    None               update         NaN   
2              11/29/2021               update         NaN   
3               8/24/2022               update         NaN   
4               8/16/2022               update         NaN   

                                          county_ids  \
0  [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14...   
1  [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14...   
2  [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14...   
3  [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14...   
4  [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14...   

                                        technologies  \
0           [BIOD, ETH, ELEC, HY, IR, NG, PHEV, LPG]   
1  [AFTMKTCONV, BIOD, ETH, ELEC, EFFEC, HEV, HY, ...   
2        [BIOD, ETH, ELEC, EFFEC, HY, NG, PHEV, LPG]   
3                               [HY, NG, OTHER, LPG]   
4  [AFTMKTCONV, ETH, ELEC, EFFEC, HY, IR, NG, PHE...   

                                          categories  \
0  [{'code': 'STATION', 'title': 'Alternative Fue...   
1  [{'code': 'AFTMKTCONV', 'title': 'Aftermarket ...   
2  [{'code': 'BIOD', 'title': 'Biodiesel', 'categ...   
3  [{'code': 'STATION', 'title': 'Alternative Fue...   
4  [{'code': 'AFTMKTCONV', 'title': 'Aftermarket ...   

                                               types  \
0  [{'id': 8, 'title': 'Incentives', 'code': 'INC'}]   
1   [{'id': 9, 'title': 'Programs', 'code': 'PROG'}]   
2  [{'id': 8, 'title': 'Incentives', 'code': 'INC'}]   
3  [{'id': 8, 'title': 'Incentives', 'code': 'INC'}]   
4  [{'id': 8, 'title': 'Incentives', 'code': 'INC'}]   

                                          references topics  
0  [{'description': 'Public Law 117-58', 'url': '...     []  
1                                                 []     []  
2  [{'description': 'Public Law 117-58', 'url': '...     []  
3  [{'description': '26 U.S. Code 6426', 'url': '...     []  
4  [{'description': 'Public Law 117-58', 'url': '...     []

In [10]:
#We are interested in having an amount of all different types of incentives and regulations per state.
reduced_df=incentives_df[["id","state","type"]]
#drop empty values "type" values:
reduced_df=reduced_df.loc[reduced_df["type"]!=""].copy()
reduced_df

id state                        type
0       284    US                  Incentives
1       288    US                    Programs
2       317    US                  Incentives
3       319    US                  Incentives
4       323    US                  Incentives
...     ...   ...                         ...
1308  13158    CO            State Incentives
1309  13159    US        Laws and Regulations
1310  13161    NY        Laws and Regulations
1311  13162    NY        Laws and Regulations
1312  13163    SD  Utility/Private Incentives

[1309 rows x 3 columns]

In [11]:
incentive_types_df=pd.DataFrame(index=reduced_df["state"].unique())
for type in reduced_df["type"].unique():
    incentive_types_df[type]=reduced_df.loc[reduced_df["type"]==type].groupby("state").count()["id"]
incentive_types_df.head()

Incentives  Programs  Laws and Regulations  State Incentives  \
US        37.0       4.0                    20               NaN   
AZ         NaN       NaN                    13               6.0   
CA         NaN       NaN                    61              41.0   
CO         NaN       NaN                    25              13.0   
DC         NaN       NaN                    13               4.0   

    Utility/Private Incentives  
US                         NaN  
AZ                        13.0  
CA                        52.0  
CO                        14.0  
DC                         2.0

In [12]:
incentive_types_df.to_csv("../Resources/incentives.csv")

In [13]:
by_age = "../Input/census_by_age.csv"
by_age_df = pd.read_csv(by_age, encoding="utf-8")
by_age_df.head()

Label (Grouping) Alabama!!Total!!Estimate  \
0        Total population                5,039,877   
1                     AGE                      NaN   
2           Under 5 years                  290,091   
3            5 to 9 years                  298,540   
4          10 to 14 years                  337,730   

  Alabama!!Total!!Margin of Error Alabama!!Percent!!Estimate  \
0                           *****                        (X)   
1                             NaN                        NaN   
2                          ±3,556                       5.8%   
3                          ±7,263                       5.9%   
4                          ±8,859                       6.7%   

  Alabama!!Percent!!Margin of Error Alabama!!Male!!Estimate  \
0                               (X)               2,445,896   
1                               NaN                     NaN   
2                              ±0.1                 149,482   
3                              ±0.1                 154,786   
4                              ±0.2                 168,349   

  Alabama!!Male!!Margin of Error Alabama!!Percent Male!!Estimate  \
0                         ±5,868                             (X)   
1                            NaN                             NaN   
2                         ±2,753                            6.1%   
3                         ±5,044                            6.3%   
4                         ±5,077                            6.9%   

  Alabama!!Percent Male!!Margin of Error Alabama!!Female!!Estimate  ...  \
0                                    (X)                 2,593,981  ...   
1                                    NaN                       NaN  ...   
2                                   ±0.1                   140,609  ...   
3                                   ±0.2                   143,754  ...   
4                                   ±0.2                   169,381  ...   

  Puerto Rico!!Percent!!Estimate Puerto Rico!!Percent!!Margin of Error  \
0                            (X)                                   (X)   
1                            NaN                                   NaN   
2                           3.2%                                  ±0.1   
3                           4.6%                                  ±0.2   
4                           5.4%                                  ±0.2   

  Puerto Rico!!Male!!Estimate Puerto Rico!!Male!!Margin of Error  \
0                   1,543,991                             ±3,969   
1                         NaN                                NaN   
2                      49,739                             ±2,447   
3                      77,392                             ±4,089   
4                      88,821                             ±3,810   

  Puerto Rico!!Percent Male!!Estimate  \
0                                 (X)   
1                                 NaN   
2                                3.2%   
3                                5.0%   
4                                5.8%   

  Puerto Rico!!Percent Male!!Margin of Error Puerto Rico!!Female!!Estimate  \
0                                        (X)                     1,719,593   
1                                        NaN                           NaN   
2                                       ±0.2                        54,102   
3                                       ±0.3                        72,805   
4                                       ±0.2                        87,621   

  Puerto Rico!!Female!!Margin of Error Puerto Rico!!Percent Female!!Estimate  \
0                               ±3,969                                   (X)   
1                                  NaN                                   NaN   
2                               ±2,956                                  3.1%   
3                               ±4,061                                  4.2%   
4                               ±4,615                                  5.1%   

  Puerto 

In [14]:
new_df=pd.DataFrame()
for column in by_age_df.columns:
    if "Label (Grouping)" in column:
        new_df[column]=by_age_df[column]
    if "Total!!Estimate" in column:
        new_df[column]=by_age_df[column]
transposed_df = new_df.set_index('Label (Grouping)').transpose()
transposed_df=transposed_df.reset_index()
transposed_df.head()

Label (Grouping)                        index Total population     AGE  \
0                    Alabama!!Total!!Estimate        5,039,877     NaN   
1                     Alaska!!Total!!Estimate          732,673     NaN   
2                    Arizona!!Total!!Estimate        7,276,316     NaN   
3                   Arkansas!!Total!!Estimate        3,025,891     NaN   
4                 California!!Total!!Estimate       39,237,836     NaN   

Label (Grouping)         Under 5 years         5 to 9 years  \
0                              290,091              298,540   
1                               46,198               52,071   
2                              402,255              446,309   
3                              179,924              196,276   
4                            2,210,235            2,358,988   

Label (Grouping)         10 to 14 years         15 to 19 years  \
0                               337,730                338,347   
1                                52,507                 50,263   
2                               476,245                482,998   
3                               204,485                206,963   
4                             2,647,372              2,579,680   

Label (Grouping)         20 to 24 years         25 to 29 years  \
0                               323,961                314,216   
1                                45,855                 54,764   
2                               488,212                502,697   
3                               200,480                184,424   
4                             2,531,692              2,825,980   

Label (Grouping)         30 to 34 years  ...         75 years and over  \
0                               319,367  ...                   345,586   
1                                57,577  ...                    31,119   
2                               497,839  ...                   549,618   
3                               200,352  ...                   210,523   
4                             3,001,889  ...                 2,395,322   

Label (Grouping)     SUMMARY INDICATORS         Median age (years)  \
0                                   NaN                       39.8   
1                                   NaN                       35.6   
2                                   NaN                       38.6   
3                                   NaN                       38.5   
4                                   NaN                       37.6   

Label (Grouping)         Sex ratio (males per 100 females)  \
0                                                     94.3   
1                                                    109.6   
2                                                     99.5   
3                                                     97.5   
4                                                    100.0   

Label (Grouping)         Age dependency ratio  \
0                                        66.1   
1                                        61.1   
2                                        68.1   
3                                        68.4   
4                                        60.1   

Label (Grouping)         Old-age dependency ratio  \
0                                            29.2   
1                                            21.6   
2                                            30.8   
3                                            29.2   
4                                            24.3   

Label (Grouping)         Child dependency ratio     PERCENT ALLOCATED  \
0                                          36.9                   NaN   
1                                          39.4                   NaN   
2                                          37.3                   NaN   
3                                          39.2                   NaN   
4                                          35.8                   NaN   

Label (Grouping)         Sex         Age  
0                        (X)         (X)  
1   

In [15]:
# transposed_df = pd.to_numeric(transposed_df.iloc[:,3])
transposed_df.iloc[:,2] = transposed_df.iloc[:,2].str.replace(",","")
transposed_df.iloc[:,3] = transposed_df.iloc[:,3].str.replace(",","")
transposed_df.iloc[:,4] = transposed_df.iloc[:,4].str.replace(",","")
transposed_df.iloc[:,5] = transposed_df.iloc[:,5].str.replace(",","")
transposed_df.iloc[:,6] = transposed_df.iloc[:,6].str.replace(",","")
transposed_df.iloc[:,7] = transposed_df.iloc[:,7].str.replace(",","")
transposed_df.iloc[:,8] = transposed_df.iloc[:,8].str.replace(",","")
transposed_df.iloc[:,9] = transposed_df.iloc[:,9].str.replace(",","")
transposed_df.iloc[:,10] = transposed_df.iloc[:,10].str.replace(",","")
transposed_df.iloc[:,11] = transposed_df.iloc[:,11].str.replace(",","")
transposed_df.iloc[:,12] = transposed_df.iloc[:,12].str.replace(",","")
transposed_df.iloc[:,13] = transposed_df.iloc[:,13].str.replace(",","")
transposed_df.iloc[:,14] = transposed_df.iloc[:,14].str.replace(",","")
transposed_df.iloc[:,15] = transposed_df.iloc[:,15].str.replace(",","")
transposed_df.iloc[:,16] = transposed_df.iloc[:,16].str.replace(",","")
transposed_df.iloc[:,17] = transposed_df.iloc[:,17].str.replace(",","")
transposed_df.iloc[:,18] = transposed_df.iloc[:,18].str.replace(",","")
transposed_df.iloc[:,19] = transposed_df.iloc[:,19].str.replace(",","")


transposed_df.iloc[:,2] = pd.to_numeric(transposed_df.iloc[:,2])
transposed_df.iloc[:,3] = pd.to_numeric(transposed_df.iloc[:,3])
transposed_df.iloc[:,4] = pd.to_numeric(transposed_df.iloc[:,4])
transposed_df.iloc[:,5] = pd.to_numeric(transposed_df.iloc[:,5])
transposed_df.iloc[:,6] = pd.to_numeric(transposed_df.iloc[:,6])
transposed_df.iloc[:,7] = pd.to_numeric(transposed_df.iloc[:,7])
transposed_df.iloc[:,8] = pd.to_numeric(transposed_df.iloc[:,8])
transposed_df.iloc[:,9] = pd.to_numeric(transposed_df.iloc[:,9])
transposed_df.iloc[:,10] = pd.to_numeric(transposed_df.iloc[:,10])
transposed_df.iloc[:,10] = pd.to_numeric(transposed_df.iloc[:,10])
transposed_df.iloc[:,11] = pd.to_numeric(transposed_df.iloc[:,11])
transposed_df.iloc[:,12] = pd.to_numeric(transposed_df.iloc[:,12])
transposed_df.iloc[:,13] = pd.to_numeric(transposed_df.iloc[:,13])
transposed_df.iloc[:,14] = pd.to_numeric(transposed_df.iloc[:,14])
transposed_df.iloc[:,15] = pd.to_numeric(transposed_df.iloc[:,15])
transposed_df.iloc[:,16] = pd.to_numeric(transposed_df.iloc[:,16])
transposed_df.iloc[:,17] = pd.to_numeric(transposed_df.iloc[:,17])
transposed_df.iloc[:,18] = pd.to_numeric(transposed_df.iloc[:,18])
transposed_df.iloc[:,19] = pd.to_numeric(transposed_df.iloc[:,19])


In [16]:
transposed_df["index"]=transposed_df["index"].str.replace('!!Total!!Estimate','')


In [17]:
transposed_df=transposed_df.rename(columns={"index":"State"})

In [18]:
transposed_df['0 - 10'] = transposed_df.iloc[:,3] + transposed_df.iloc[:,4]
transposed_df['11 - 20'] = transposed_df.iloc[:,5] + transposed_df.iloc[:,6]
transposed_df['21 - 30'] = transposed_df.iloc[:,7] + transposed_df.iloc[:,8]
transposed_df['31 - 40'] = transposed_df.iloc[:,8] + transposed_df.iloc[:,9]
transposed_df['41 - 50'] = transposed_df.iloc[:,9] + transposed_df.iloc[:,10]
transposed_df['51 - 60'] = transposed_df.iloc[:,11] + transposed_df.iloc[:,12]
transposed_df['61 - 70'] = transposed_df.iloc[:,13] + transposed_df.iloc[:,14]
transposed_df['70+'] = transposed_df.iloc[:,15] + transposed_df.iloc[:,16]


transposed_df=transposed_df[[
    "State","0 - 10","11 - 20","21 - 30","31 - 40","41 - 50","51 - 60","61 - 70","70+"
]]
transposed_df.head()

Label (Grouping)       State   0 - 10  11 - 20  21 - 30  31 - 40  41 - 50  \
0                    Alabama   588631   676077   638177   633583   630402   
1                     Alaska    98269   102770   100619   112341   112453   
2                    Arizona   848564   959243   990909  1000536   967684   
3                   Arkansas   376200   411448   384904   384776   397667   
4                 California  4569223  5227052  5357672  5827869  5794592   

Label (Grouping)  51 - 60  61 - 70      70+  
0                  628011   650556   633120  
1                   88233    85277    87424  
2                  864493   854742   866925  
3                  361972   377222   358151  
4                 5052065  4945507  4279995

In [19]:
transposed_df.dtypes

Label (Grouping)
State      object
0 - 10      int64
11 - 20     int64
21 - 30     int64
31 - 40     int64
41 - 50     int64
51 - 60     int64
61 - 70     int64
70+         int64
dtype: object

In [20]:
transposed_df.to_csv("../Resources/new_by_age.csv",index = False, header = True)

In [21]:
c=Census(majo_api,
        year=2021)

In [22]:
education_data = c.acs5.get(
    (
        "NAME",
        "B15003_002E",
        "B15003_017E",
        "B15003_018E",
        "B15003_021E",
        "B15003_022E",
        "B15003_023E",
        "B15003_024E",
        "B15003_025E",
        "B01002_001E"
    ),
    {'for': 'state:*'}
)

education_df=pd.DataFrame(education_data)

education_df=education_df.rename(
    columns = {
        "NAME":"State",
        "B15003_002E":"No education",
        "B15003_017E":"High School",
        "B15003_018E":"GED or alternative",
        "B15003_021E":"associates",
        "B15003_022E":"Bachelors",
        "B15003_023E":"Masters",
        "B15003_024E":"Professional",
        "B15003_025E":"Doctorate",
        "B01002_001E":"age"
    }
)

# census_pd["Poverty Rate"]=100*census_pd["Poverty Count"].astype(int) / census_pd["Population"].astype(int)

education_df=education_df[
    [
        "State",
        "No education",
        "High School",
        "GED or alternative",
        "associates",
        "Bachelors",
        "Masters",
        "Professional",
        "Doctorate",
        "age"
    ]
]

#Display DataFrame
print(f"Number of rows in the DataFrame:){len(education_df)}")
education_df.head()

Number of rows in the DataFrame:)52


State  No education  High School  GED or alternative  associates  \
0     Alabama       43813.0     864345.0            176864.0    303299.0   
1      Alaska        3675.0     111772.0             26101.0     41808.0   
2     Arizona       74688.0     934136.0            191362.0    433004.0   
3    Arkansas       26523.0     566668.0            122064.0    154675.0   
4  California      820953.0    4836799.0            640355.0   2135865.0   

   Bachelors    Masters  Professional  Doctorate   age  
0   563628.0   251040.0       54076.0    41681.0  39.3  
1    92691.0    39503.0        9969.0     6028.0  35.0  
2   923339.0   413353.0       92301.0    66423.0  38.1  
3   313527.0   129009.0       29370.0    19363.0  38.3  
4  5855383.0  2449563.0      678258.0   468234.0  37.0

In [23]:
education_df.to_csv("../Resources/education_data.csv", encoding="utf-8", index=False)

In [24]:
income_data = c.acs5.get(
    (
        "NAME",
        "B19013_001E",
        "B19301_001E"
    ),
    {'for': 'state:*'}
)

income_df=pd.DataFrame(income_data)

income_df=income_df.rename(
    columns = {
        "NAME":"State",
        "B19013_001E":"Income",
        "B19301_001E":"Income Per Capita"
    }
)

income_df=income_df[
    [
        "State",
        "Income",
        "Income Per Capita" 
    ]
]


In [25]:
income_df.head()

State   Income  Income Per Capita
0     Alabama  54943.0            30458.0
1      Alaska  80287.0            39236.0
2     Arizona  65913.0            34644.0
3    Arkansas  52123.0            29210.0
4  California  84097.0            41276.0

In [26]:
labels=["low","medium","high"]
income_cut = pd.cut(income_df["Income Per Capita"], 3,labels=labels)
income_df["Income Category"]=income_cut

In [27]:
income_df=income_df[["State","Income Per Capita","Income Category"]]
income_df.head()

State  Income Per Capita Income Category
0     Alabama            30458.0             low
1      Alaska            39236.0          medium
2     Arizona            34644.0          medium
3    Arkansas            29210.0             low
4  California            41276.0          medium

In [28]:
income_df.to_csv("../Resources/income_data.csv",encoding="utf-8",index=False)

In [29]:
# Read in the presidential elections data set
pres_electionsdata = pd.read_csv('../Input/presidential_elections.csv')
pres_electionsdata.head()

year    state state_po  state_fips  state_cen  state_ic        office  \
0  1976  ALABAMA       AL           1         63        41  US PRESIDENT   
1  1976  ALABAMA       AL           1         63        41  US PRESIDENT   
2  1976  ALABAMA       AL           1         63        41  US PRESIDENT   
3  1976  ALABAMA       AL           1         63        41  US PRESIDENT   
4  1976  ALABAMA       AL           1         63        41  US PRESIDENT   

                 candidate              party_detailed writein  \
0            CARTER, JIMMY                    DEMOCRAT   False   
1             FORD, GERALD                  REPUBLICAN   False   
2           MADDOX, LESTER  AMERICAN INDEPENDENT PARTY   False   
3  BUBAR, BENJAMIN ""BEN""                 PROHIBITION   False   
4                HALL, GUS         COMMUNIST PARTY USE   False   

   candidatevotes  totalvotes   version  notes party_simplified  
0          659170     1182850  20210113    NaN         DEMOCRAT  
1          504070     1182850  20210113    NaN       REPUBLICAN  
2            9198     1182850  20210113    NaN            OTHER  
3            6669     1182850  20210113    NaN            OTHER  
4            1954     1182850  20210113    NaN            OTHER

In [30]:
# Get the information on the DataFrame
pres_electionsdata.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4287 entries, 0 to 4286
Data columns (total 15 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   year              4287 non-null   int64  
 1   state             4287 non-null   object 
 2   state_po          4287 non-null   object 
 3   state_fips        4287 non-null   int64  
 4   state_cen         4287 non-null   int64  
 5   state_ic          4287 non-null   int64  
 6   office            4287 non-null   object 
 7   candidate         4000 non-null   object 
 8   party_detailed    3831 non-null   object 
 9   writein           4284 non-null   object 
 10  candidatevotes    4287 non-null   int64  
 11  totalvotes        4287 non-null   int64  
 12  version           4287 non-null   int64  
 13  notes             0 non-null      float64
 14  party_simplified  4287 non-null   object 
dtypes: float64(1), int64(7), object(7)
memory usage: 502.5+ KB


In [31]:
# Group the data by state and year, and find the candidate with the most votes and their corresponding party
winners = pres_electionsdata.groupby(['year', 'state'])[['candidatevotes', 'party_simplified']].apply(lambda x: x.loc[x['candidatevotes'].idxmax()])
# Reset the index to create a DataFrame with the state, year and winning party
winners = winners.reset_index()[['state', 'year','party_simplified']]
winners.head()

state  year party_simplified
0     ALABAMA  1976         DEMOCRAT
1      ALASKA  1976       REPUBLICAN
2     ARIZONA  1976       REPUBLICAN
3    ARKANSAS  1976         DEMOCRAT
4  CALIFORNIA  1976       REPUBLICAN

In [32]:
# Create a new DataFrame with a column for each party and a row for each state
state_party_counts = pd.crosstab(winners['state'], winners['party_simplified'])

# Rename the columns to match the desired output
state_party_counts = state_party_counts.rename(columns={'DEMOCRAT': 'Democrat', 'REPUBLICAN': 'Republican'})

# Reset the index to make 'state' a column
state_party_counts = state_party_counts.reset_index()

# Add a new column to indicate the party with the most wins in each state
state_party_counts['Most Wins'] = np.where((state_party_counts['Democrat'] - state_party_counts['Republican']).abs() < 3,
                                            'Neutral',
                                            np.where(state_party_counts['Democrat'] > state_party_counts['Republican'],
                                                     'Democrat',
                                                     'Republican'))
# Display the updated DataFrame

state_party_counts.to_csv('../Resources/state_party_counts.csv', index=False)

state_party_counts

party_simplified                 state  Democrat  Republican   Most Wins
0                              ALABAMA         1          11  Republican
1                               ALASKA         0          12  Republican
2                              ARIZONA         2          10  Republican
3                             ARKANSAS         3           9  Republican
4                           CALIFORNIA         8           4    Democrat
5                             COLORADO         5           7     Neutral
6                          CONNECTICUT         8           4    Democrat
7                             DELAWARE         9           3    Democrat
8                 DISTRICT OF COLUMBIA        12           0    Democrat
9                              FLORIDA         4           8  Republican
10                             GEORGIA         4           8  Republican
11                              HAWAII        11           1    Democrat
12                               IDAHO         0          12  Republican
13                            ILLINOIS         8           4    Democrat
14                             INDIANA         1          11  Republican
15                                IOWA         6           6     Neutral
16                              KANSAS         0          12  Republican
17                            KENTUCKY         3           9  Republican
18                           LOUISIANA         3           9  Republican
19                               MAINE         8           4    Democrat
20                            MARYLAND        10           2    Democrat
21                       MASSACHUSETTS        10           2    Democrat
22                            MICHIGAN         7           5     Neutral
23                           MINNESOTA        12           0    Democrat
24                         MISSISSIPPI         1          11  Republican
25                            MISSOURI         3           9  Republican
26                             MONTANA         1          11  Republican
27                            NEBRASKA         0          12  Republican
28                              NEVADA         6           6     Neutral
29                       NEW HAMPSHIRE         7           5     Neutral
30                          NEW JERSEY         8           4    Democrat
31                          NEW MEXICO         7           5     Neutral
32                            NEW YORK        11           1    Democrat
33                      NORTH CAROLINA         2          10  Republican
34                        NORTH DAKOTA         0          12  Republican
35                                OHIO         5           7     Neutral
36                            OKLAHOMA         0          12  Republican
37                              OREGON         9           3    Democrat
38                        PENNSYLVANIA         8           4    Democrat
39                        RHODE ISLAND        11           1    Democrat
40                      SOUTH CAROLINA         1          11  Republican
41                        SOUTH DAKOTA         0          12  Republican
42                           TENNESSEE         3           9  Republican
43                               TEXAS         1          11  Republican
44                                UTAH         0          12  Republican
45                             VERMONT         8           4    Democrat
46                            VIRGINIA         4           8  Republican
47                          WASHINGTON         9           3    Democrat
48                       WEST VIRGINIA         5           7     Neutral
49                           WISCONSIN         9           3    Democrat
50                             WYOMING         0          12  Republican

In [33]:
# Create a boolean mask to filter elections of 2000 and after
filter = winners['year'] >= 2000

# Filter the winners DataFrame using the mask
winners_2000 = winners[filter]

# Create a new DataFrame with a column for each party and a row for each state
state_party_counts_2000 = pd.crosstab(winners_2000['state'], winners_2000['party_simplified'])

# Rename the columns to match the desired output
state_party_counts_2000 = state_party_counts_2000.rename(columns={'DEMOCRAT': 'Democrat', 'REPUBLICAN': 'Republican'})

# Reset the index to make 'state' a column
state_party_counts_2000 = state_party_counts_2000.reset_index()

# Add a new column to indicate the party with the most wins in each state
state_party_counts_2000['Most Wins'] = np.where((state_party_counts_2000['Democrat'] - state_party_counts_2000['Republican']).abs() < 3,
                                                'Neutral',
                                                np.where(state_party_counts_2000['Democrat'] > state_party_counts_2000['Republican'],
                                                         'Democrat',
                                                         'Republican'))

# Display the updated DataFrame
state_party_counts_2000.to_csv('../Resources/state_party_counts_2000.csv', index=False)
state_party_counts_2000


party_simplified                 state  Democrat  Republican   Most Wins
0                              ALABAMA         0           6  Republican
1                               ALASKA         0           6  Republican
2                              ARIZONA         1           5  Republican
3                             ARKANSAS         0           6  Republican
4                           CALIFORNIA         6           0    Democrat
5                             COLORADO         4           2     Neutral
6                          CONNECTICUT         6           0    Democrat
7                             DELAWARE         6           0    Democrat
8                 DISTRICT OF COLUMBIA         6           0    Democrat
9                              FLORIDA         2           4     Neutral
10                             GEORGIA         1           5  Republican
11                              HAWAII         6           0    Democrat
12                               IDAHO         0           6  Republican
13                            ILLINOIS         6           0    Democrat
14                             INDIANA         1           5  Republican
15                                IOWA         3           3     Neutral
16                              KANSAS         0           6  Republican
17                            KENTUCKY         0           6  Republican
18                           LOUISIANA         0           6  Republican
19                               MAINE         6           0    Democrat
20                            MARYLAND         6           0    Democrat
21                       MASSACHUSETTS         6           0    Democrat
22                            MICHIGAN         5           1    Democrat
23                           MINNESOTA         6           0    Democrat
24                         MISSISSIPPI         0           6  Republican
25                            MISSOURI         0           6  Republican
26                             MONTANA         0           6  Republican
27                            NEBRASKA         0           6  Republican
28                              NEVADA         4           2     Neutral
29                       NEW HAMPSHIRE         5           1    Democrat
30                          NEW JERSEY         6           0    Democrat
31                          NEW MEXICO         5           1    Democrat
32                            NEW YORK         6           0    Democrat
33                      NORTH CAROLINA         1           5  Republican
34                        NORTH DAKOTA         0           6  Republican
35                                OHIO         2           4     Neutral
36                            OKLAHOMA         0           6  Republican
37                              OREGON         6           0    Democrat
38                        PENNSYLVANIA         5           1    Democrat
39                        RHODE ISLAND         6           0    Democrat
40                      SOUTH CAROLINA         0           6  Republican
41                        SOUTH DAKOTA         0           6  Republican
42                           TENNESSEE         0           6  Republican
43                               TEXAS         0           6  Republican
44                                UTAH         0           6  Republican
45                             VERMONT         6           0    Democrat
46                            VIRGINIA         4           2     Neutral
47                          WASHINGTON         6           0    Democrat
48                       WEST VIRGINIA         0           6  Republican
49                           WISCONSIN         5           1    Democrat
50                             WYOMING         0           6  Republican